In [1]:
try:
    import evidently
except:
    !pip install git+https://github.com/evidentlyai/evidently.git

In [2]:
import pandas as pd
import numpy as np

from evidently import ColumnMapping

from evidently.report import Report
from evidently.metrics.base_metric import generate_column_metrics
from evidently.metric_preset import DataDriftPreset, TargetDriftPreset, DataQualityPreset, RegressionPreset
from evidently.metrics import *

from evidently.test_suite import TestSuite
from evidently.tests.base_test import generate_column_tests
from evidently.test_preset import DataStabilityTestPreset, NoTargetPerformanceTestPreset, RegressionTestPreset
from evidently.tests import *

C:\Users\Raider\AppData\Local\Programs\Python\Python311\Lib\site-packages\umap\distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
C:\Users\Raider\AppData\Local\Programs\Python\Python311\Lib\site-packages\umap\distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
C:\Users\Raider\AppData\Local\Programs\Python\Pyth

In [3]:
import warnings
warnings.filterwarnings('ignore')
warnings.simplefilter('ignore')

# Chargement des données

In [4]:
# Charger le DataFrame application_train
application_train = pd.read_csv('data/application_train.csv', index_col="SK_ID_CURR", encoding="utf-8")

# Créer un nouveau DataFrame 'trained_data' sans la colonne 'TARGET'
trained_data = application_train.drop(columns=['TARGET'])

# Charger le DataFrame application_test
application_test = pd.read_csv('data/application_test.csv', index_col="SK_ID_CURR", encoding="utf-8")

# Afficher la forme des DataFrames
print(trained_data.shape)
print(application_test.shape)


(307511, 120)
(48744, 120)


In [5]:
reference = trained_data.sample(n=40000, replace=False)
current = application_test.sample(n=40000, replace=False)

In [6]:

# Charger le DataFrame application_train
application_train = pd.read_csv('data/application_train.csv', encoding="utf-8")

# Créer un nouveau DataFrame 'trained_data' sans la colonne 'TARGET'
trained_data = application_train.drop(columns=['TARGET'])

# Charger le DataFrame application_test
application_test = pd.read_csv('data/application_test.csv', encoding="utf-8")

# Afficher la forme des DataFrames
print(trained_data.shape)
print(application_test.shape)

# Create a reference DataFrame if needed
reference = trained_data.sample(n=5000, replace=False)

# Create a current DataFrame if needed (you can replace this with application_test if you want to compare with test data)
current = application_test.sample(n=5000, replace=False)


(307511, 121)
(48744, 121)


In [7]:
report1 = Report(metrics=[
    DataDriftPreset(), 
])

report1.run(reference_data=reference, current_data=current)
report1

In [8]:
report1.save_html('report1.html')

In [9]:
report1.as_dict()

{'metrics': [{'metric': 'DatasetDriftMetric',
   'result': {'drift_share': 0.5,
    'number_of_columns': 121,
    'number_of_drifted_columns': 9,
    'share_of_drifted_columns': 0.0743801652892562,
    'dataset_drift': False}},
  {'metric': 'DataDriftTable',
   'result': {'number_of_columns': 121,
    'number_of_drifted_columns': 9,
    'share_of_drifted_columns': 0.0743801652892562,
    'dataset_drift': False,
    'drift_by_columns': {'AMT_ANNUITY': {'column_name': 'AMT_ANNUITY',
      'column_type': 'num',
      'stattest_name': 'Wasserstein distance (normed)',
      'stattest_threshold': 0.1,
      'drift_score': 0.1880010853362059,
      'drift_detected': True,
      'current': {'small_distribution': {'x': [2295.0,
         19671.75,
         37048.5,
         54425.25,
         71802.0,
         89178.75,
         106555.5,
         123932.25,
         141309.0,
         158685.75,
         176062.5],
        'y': [1.8019782185969184e-05,
         2.5112552682171753e-05,
         

In [10]:
report1.json()

'{"version": "0.3.3", "timestamp": "2023-07-18 00:22:25.802922", "metrics": [{"metric": "DatasetDriftMetric", "result": {"drift_share": 0.5, "number_of_columns": 121, "number_of_drifted_columns": 9, "share_of_drifted_columns": 0.0743801652892562, "dataset_drift": false}}, {"metric": "DataDriftTable", "result": {"number_of_columns": 121, "number_of_drifted_columns": 9, "share_of_drifted_columns": 0.0743801652892562, "dataset_drift": false, "drift_by_columns": {"AMT_ANNUITY": {"column_name": "AMT_ANNUITY", "column_type": "num", "stattest_name": "Wasserstein distance (normed)", "stattest_threshold": 0.1, "drift_score": 0.1880010853362059, "drift_detected": true, "current": {"small_distribution": {"x": [2295.0, 19671.75, 37048.5, 54425.25, 71802.0, 89178.75, 106555.5, 123932.25, 141309.0, 158685.75, 176062.5], "y": [1.8019782185969184e-05, 2.5112552682171753e-05, 9.94830147519321e-06, 3.4312428699161765e-06, 5.641976531070224e-07, 3.6845561019234113e-07, 4.605695127404264e-08, 4.6056951274

In [11]:
report1.save_json('report.json')

In [12]:
display(report1)

In [13]:
tests = TestSuite(tests=[
    TestNumberOfColumnsWithMissingValues(),
    TestNumberOfRowsWithMissingValues(),
    TestNumberOfConstantColumns(),
    TestNumberOfDuplicatedRows(),
    TestNumberOfDuplicatedColumns(),
    TestColumnsType(),
    TestNumberOfDriftedColumns(),
])

tests.run(reference_data=reference, current_data=current)
tests

In [14]:
tests.save_html('tests.html')